# iGaming retention test

> Data Generator A/B groups using Python
> 
> Two group of people splitted, between treatment and control group

In [1]:
# Step 1: importing libraries
import numpy as np
import pandas as pd

In [2]:
# Setting seed and number of players
np.random.seed(69)
n = 70000

In [3]:
# Step 2: Group assignment
groups = np.random.choice(['control', 'treatment'], size = n)

# Step 3: Base engagement metrics (for both groups)
sessions = np.random.poisson(lam = 5, size = n) + (groups == 'treatment') * np.random.poisson(lam = 2, size = n)

# Step 4: Deposits
base_deposits = np.random.gamma(shape = 2, scale = 50, size = n)
treatment_boost = (groups == 'treatment') * np.random.normal(20, 10, size = n)
deposits = np.clip(base_deposits + treatment_boost, 0, None)

# Step 5: Feature usage (higher in treatment)
feature_used = np.where(groups == 'treatment', np.random.binomial(1, 0.7, size = n), np.random.binomial(1, 0.4, size = n))

In [4]:
# Step 6: Churn generation: different in treatment group
churn_prob = 0.45 - 0.08 * (groups == 'treatment') - 0.03 * feature_used - 0.01 * (sessions > 6)
churn_prob = np.clip(churn_prob, 0.1, 0.9)
churn = np.random.binomial(1, churn_prob)

In [5]:
# Step 7: assemble dataset and print it
df = pd.DataFrame({
    'user_id': np.arange(1, n + 1),
    'group': groups,
    'sessions': sessions,
    'deposits': np.round(deposits, 2),
    'feature_used': feature_used,
    'churn': churn,
})
df.to_csv('simulated_users.csv', index = False)
print('✅ Simulated data saved to simulated_users.csv')

✅ Simulated data saved to simulated_users.csv


# Analysing CSV file with SQL

> Using SQLite and Pandas

In [6]:
# Step 1: importing libraries
import pandas as pd
import sqlite3

# Step 2: Defining file and table
csv_file = "simulated_users.csv"
table_name = "player_data"
db_file = "player_data.db"

# Step 3: Loading CSV into DataFrame
df = pd.read_csv(csv_file)

# Step 4: Renaming group column to user_group for safety
if 'group' in df.columns:
    df = df.rename(columns={'group': 'user_group'})
elif 'user_group' not in df.columns:
    raise ValueError("CSV missing 'group' or 'user_group' column")

# Step 5: Connecing to SQLite and creating / replacing table
conn = sqlite3.connect(db_file)
df.to_sql(table_name, conn, if_exists='replace', index=False)

# Step 6: Writing SQL query retention and churn aggregation per user group
query = """
SELECT
  user_group,
  COUNT(*) AS total_players,
  SUM(churn) AS churned,
  SUM(1 - churn) AS retained,
  ROUND(100.0 * SUM(1 - churn) / COUNT(*), 2) AS retention_rate_pct
FROM player_data
GROUP BY user_group;
"""

# Step 7: Executing query and loading to DataFrame
result = pd.read_sql(query, conn)
conn.close()

# Step 8: Showing results
print("📊 Retention Analysis Results:")
print(result)

📊 Retention Analysis Results:
  user_group  total_players  churned  retained  retention_rate_pct
0    control          34891    15242     19649               56.32
1  treatment          35109    12024     23085               65.75


# Statistical testing of retention difference
> Python and Scipy library

In [7]:
# Step 1: importing scipy for the stats
from scipy.stats import chi2_contingency

# Step 2: Connecting again for the retention difference
conn = sqlite3.connect('player_data.db')
df = pd.read_sql("SELECT user_group, churn FROM player_data", conn)
conn.close()

# Step 3: Testing Contingency table for Chi-square test
contingency = pd.crosstab(df['user_group'], 1 - df['churn'])
chi2, p_value, _, _ = chi2_contingency(contingency)

# Step 4: Printing results
print(f"✅ Chi-square test for retention difference")
print(f"Chi-square statistic: {chi2:.2f}")
print(f"P-value: {p_value:.4f}")

✅ Chi-square test for retention difference
Chi-square statistic: 655.00
P-value: 0.0000


# Logistic Regression ML churn model
> Sklearn library

In [8]:
# Step 1: Importing libraries using SKlearn 
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import roc_auc_score, classification_report

# Step 2: Connecting sqlite3 again for regression testing 
conn = sqlite3.connect('player_data.db')
df = pd.read_sql("SELECT sessions, deposits, feature_used, churn FROM player_data", conn)
conn.close()

# Step 3: Defining Y and X values for the regression model
X = df[['sessions', 'deposits', 'feature_used']]
y = df['churn']
X_train, X_test, y_train, y_test = train_test_split(X, y, stratify=y, random_state=42, test_size=0.3)

model = LogisticRegression(max_iter=1000, class_weight='balanced')
model.fit(X_train, y_train)

# Step 4: Testing model
y_pred = model.predict(X_test)
y_prob = model.predict_proba(X_test)[:, 1]


# Step 5: Printing results
print("✅ Logistic Regression Churn Model Results")
print(f"AUC: {roc_auc_score(y_test, y_prob):.3f}")
print(classification_report(y_test, y_pred))

# Step 6: Feature importance
coef_df = pd.DataFrame({'Feature': X.columns, 'Coefficient': model.coef_[0]})
display(coef_df)

# Step 7: Export churn probabilities for visualization in Tableau
export_df = X_test.copy()
export_df['churn_probability'] = y_prob
export_df['actual_churn'] = y_test.values

export_df.to_csv('churn_probabilities.csv', index=False)
print("✅ Churn probabilities exported to churn_probabilities_export.csv")

✅ Logistic Regression Churn Model Results
AUC: 0.547
              precision    recall  f1-score   support

           0       0.64      0.56      0.60     12820
           1       0.43      0.52      0.47      8180

    accuracy                           0.54     21000
   macro avg       0.53      0.54      0.53     21000
weighted avg       0.56      0.54      0.55     21000



Feature  Coefficient
0      sessions    -0.026931
1      deposits    -0.000377
2  feature_used    -0.196687

✅ Churn probabilities exported to churn_probabilities_export.csv


# Interactive plots with Plotly
> Retention, Deposits, Churn Probabilities

In [9]:
import plotly.io as pio
pio.renderers.default = 'notebook'
import plotly.express as px
import pandas as pd

# Load step 3 and 5 outputs if fresh restarting environment
retention_summary = pd.read_csv('simulated_users.csv')
retention_summary_grouped = retention_summary.groupby('group').agg(
    retention_rate_pct=('churn', lambda x: 100 * (1 - x.mean())),
    avg_deposits=('deposits', 'mean')
).reset_index()

# Retention rate bar chart
fig1 = px.bar(retention_summary_grouped, x='group', y='retention_rate_pct',
              title='Retention Rate by User Group', color='group')
fig1.show()

# Deposit distribution box plot
fig2 = px.box(retention_summary, x='group', y='deposits',
              title='Deposit Amounts by User Group', color='group')
fig2.show()

# Churn probability histogram (from Step 5 preds if saved)
# Assume y_prob and y_test from model in script 5 are saved or rerun before
fig3 = px.histogram(y_prob, nbins=50, title="Churn Probability Distribution", labels={"value": "Predicted Churn Probability"})
fig3.show()